In [2]:
pip install geopy

Note: you may need to restart the kernel to use updated packages.


In [3]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/deep-solar-dataset/deepsolar_tract.csv


In [4]:
import os
import numpy as np
import pandas as pd
import random
import matplotlib.pyplot as plt
import seaborn as sns

from contextlib import contextmanager
from time import time
from tqdm import tqdm
import lightgbm as lgbm
import category_encoders as ce

from tensorflow.keras.utils import to_categorical
from sklearn.metrics import classification_report, log_loss, accuracy_score
from sklearn.metrics import mean_squared_error
from sklearn.model_selection import KFold

In [5]:
os.listdir('/kaggle/input/deep-solar-dataset')

['deepsolar_tract.csv']

In [6]:
pd.options.display.max_columns = None
pd.options.display.max_rows = None

In [7]:
data = pd.read_csv("/kaggle/input/deep-solar-dataset/deepsolar_tract.csv",engine='python',encoding='latin1')

In [8]:
all_columns= data.columns.tolist()
print('All column names: ')
for i in all_columns:
    print(i)

All column names: 
Unnamed: 0
tile_count
solar_system_count
total_panel_area
fips
average_household_income
county
education_bachelor
education_college
education_doctoral
education_high_school_graduate
education_less_than_high_school
education_master
education_population
education_professional_school
employed
gini_index
heating_fuel_coal_coke
heating_fuel_electricity
heating_fuel_fuel_oil_kerosene
heating_fuel_gas
heating_fuel_housing_unit_count
heating_fuel_none
heating_fuel_other
heating_fuel_solar
land_area
per_capita_income
population
population_density
poverty_family_below_poverty_level
poverty_family_count
race_asian
race_black_africa
race_indian_alaska
race_islander
race_other
race_two_more
race_white
state
total_area
unemployed
water_area
education_less_than_high_school_rate
education_high_school_graduate_rate
education_college_rate
education_bachelor_rate
education_master_rate
education_professional_school_rate
education_doctoral_rate
race_white_rate
race_black_africa_rate
race

In [9]:
data.head()

Unnamed: 0  tile_count  solar_system_count  total_panel_area         fips  \
0           0         0.0                 0.0          0.000000  27145011200   
1           1        25.0                21.0       1133.436461  27145011301   
2           2         3.0                 3.0         64.505776  27145011302   
3           3         0.0                 0.0          0.000000  27145011304   
4           4         5.0                 5.0        164.583303  27145011400   

   average_household_income          county  education_bachelor  \
0              70352.789869  Stearns County                 569   
1              61727.085202  Stearns County                 674   
2              71496.886583  Stearns County                 854   
3              86840.152755  Stearns County                 640   
4              89135.315597  Stearns County                 654   

   education_college  education_doctoral  education_high_school_graduate  \
0               1690                  13                            1757   
1               1434                 108                             767   
2               1459                  31                            1541   
3               1116                  68                            1095   
4               1314                  15                             982   

   education_less_than_high_school  education_master  education_population  \
0                              336               157                  4548   
1                              222               285                  3533   
2                              289               276                  4480   
3                              231               270                  3456   
4                              163               170                  3348   

   education_professional_school  employed  gini_index  \
0                             26      3569      0.3490   
1                             43      4795      0.4074   
2                             30      3550      0.3926   
3                             36      3483      0.3949   
4                             50      2887      0.4463   

   heating_fuel_coal_coke  heating_fuel_electricity  \
0                     200                       448   
1                      20                       379   
2                      69                       440   
3                     188                       442   
4                      96                       497   

   heating_fuel_fuel_oil_kerosene  heating_fuel_gas  \
0                              98              1720   
1                              17              1799   
2                              45              2098   
3                              61              1113   
4                              47              1202   

   heating_fuel_housing_unit_count  heating_fuel_none  heating_fuel_other  \
0                             2527                 10                  51   
1                             2230                  0                  15   
2                             2698                 29                  17   
3                             1833                 13                  16   
4                             1917                 31                  44   

   heating_fuel_solar  land_area  per_capita_income  population  \
0                   0  147.73120            26999.0        6577   
1                   0   16.61679            20951.0        8020   
2                   0   37.44482            28021.0        6971   
3                   0   75.21147            29275.0        6328   
4                   0   44.00151            32770.0        5264   

   population_density  poverty_family_below_poverty_level  \
0            44.52005                                  85   
1           482.64430                                 189   
2           186.16730                                 134   
3            84.13610                                  87   
4          

In [10]:
df = data[['tile_count','county','lat','lon']]

In [19]:
df.shape

(72537, 4)

In [11]:
# df[df['tile_count']<500]
df[df['tile_count']>500]

tile_count                  county     lat      lon
459        1463.0      Los Angeles County  34.631 -118.084
667         698.0      Los Angeles County  33.900 -118.046
1385        789.0      Los Angeles County  34.661 -118.096
1396       1623.0      Los Angeles County  34.675 -118.283
1505        601.0      Los Angeles County  34.532 -117.919
1512        865.0      Los Angeles County  34.626 -118.179
1706        549.0      Los Angeles County  34.432 -118.515
1823       1175.0      Los Angeles County  34.689 -118.210
3502        501.0          El Paso County  38.800 -104.692
3978        586.0       Miami-Dade County  25.561  -80.470
5968        592.0          Bristol County  41.725  -71.072
6074        760.0          Bristol County  41.694  -71.021
6286       1180.0        Dougherty County  31.502  -84.049
7813        652.0      San Joaquin County  37.785 -121.218
7868        598.0      San Joaquin County  38.043 -121.334
7881       1021.0      San Joaquin County  38.026 -121.246
7888        562.0      San Joaquin County  38.051 -121.384
7922        531.0      San Joaquin County  37.843 -121.237
7923        582.0      San Joaquin County  37.759 -121.361
7924        908.0      San Joaquin County  37.778 -121.486
7925        797.0      San Joaquin County  37.723 -121.505
7927        514.0      San Joaquin County  37.712 -121.444
7943        506.0      San Joaquin County  37.827 -121.287
8222        946.0        San Diego County  32.619 -116.948
8250        778.0        San Diego County  32.807 -116.750
8255       1052.0        San Diego County  32.992 -117.173
8274        508.0        San Diego County  33.042 -117.012
8282       1116.0        San Diego County  32.892 -117.045
8347        840.0        San Diego County  32.609 -117.000
8385        558.0        San Diego County  32.968 -117.205
8389       1184.0        San Diego County  32.924 -117.204
8390        676.0        San Diego County  32.969 -117.149
8410        568.0        San Diego County  32.952 -117.150
8423        512.0        San Diego County  32.801 -117.163
8432        508.0        San Diego County  32.800 -117.147
8445        535.0        San Diego County  32.807 -117.061
8447        958.0        San Diego County  32.790 -117.050
8500        559.0        San Diego County  32.660 -117.013
8543        694.0        San Diego County  32.815 -116.993
8554        596.0        San Diego County  32.851 -116.959
8557        658.0        San Diego County  32.838 -116.948
8559        722.0        San Diego County  32.869 -116.847
8561        718.0        San Diego County  32.835 -116.919
8565        822.0        San Diego County  32.900 -116.959
8570        634.0        San Diego County  33.040 -117.045
8573       1928.0        San Diego County  33.037 -117.124
8575       1055.0        San Diego County  33.011 -117.101
8584        543.0        San Diego County  32.927 -117.105
8592        808.0        San Diego County  32.998 -117.034
8593        660.0        San Diego County  32.991 -117.044
8596        650.0        San Diego County  33.016 -117.205
8598        817.0        San Diego County  33.078 -117.233
8599       1167.0        San Diego County  33.068 -117.177
8628        522.0        San Diego County  33.216 -117.309
8638        827.0        San Diego County  33.292 -117.270
8642        802.0        San Diego County  33.354 -117.423
8644       1035.0        San Diego County  33.331 -117.204
8649        524.0        San Diego County  33.433 -117.327
8652        586.0        San Diego County  33.227 -117.095
8663        539.0        San Diego County  33.239 -117.256
8676        739.0        San Diego County  33.153 -117.272
8682       1139.0        San Diego County  33.116 -117.247
8685        861.0        San Diego County  33.077 -117.253
8692       1199.0        San Diego County  33.111 -117.193
8695        936.0        San Diego County  33.181 -117.049
8710        512.0        San Diego County  33.082 -117.087
8714       1099.0        San Diego County  33.099 -117

In [12]:
counties_in_illinois = [
    "Adams County",
    "Alexander County",
    "Bond County",
    "Boone County",
    "Brown County",
    "Bureau County",
    "Calhoun County",
    "Carroll County",
    "Cass County",
    "Champaign County",
    "Christian County",
    "Clark County",
    "Clay County",
    "Clinton County",
    "Coles County",
    "Cook County",
    "Crawford County",
    "Cumberland County",
    "DeKalb County",
    "De Witt County",
    "Douglas County",
    "DuPage County",
    "Edgar County",
    "Edwards County",
    "Effingham County",
    "Fayette County",
    "Ford County",
    "Franklin County",
    "Fulton County",
    "Gallatin County",
    "Greene County",
    "Grundy County",
    "Hamilton County",
    "Hancock County",
    "Hardin County",
    "Henderson County",
    "Henry County",
    "Iroquois County",
    "Jackson County",
    "Jasper County",
    "Jefferson County",
    "Jersey County",
    "Jo Daviess County",
    "Johnson County",
    "Kane County",
    "Kankakee County",
    "Kendall County",
    "Knox County",
    "LaSalle County",
    "Lake County",
    "Lawrence County",
    "Lee County",
    "Livingston County",
    "Logan County",
    "McDonough County",
    "McHenry County",
    "McLean County",
    "Macon County",
    "Macoupin County",
    "Madison County",
    "Marion County",
    "Marshall County",
    "Mason County",
    "Massac County",
    "Menard County",
    "Mercer County",
    "Monroe County",
    "Montgomery County",
    "Morgan County",
    "Moultrie County",
    "Ogle County",
    "Peoria County",
    "Perry County",
    "Piatt County",
    "Pike County",
    "Pope County",
    "Pulaski County",
    "Putnam County",
    "Randolph County",
    "Richland County",
    "Rock Island County",
    "St. Clair County",
    "Saline County",
    "Sangamon County",
    "Schuyler County",
    "Scott County",
    "Shelby County",
    "Stark County",
    "Stephenson County",
    "Tazewell County",
    "Union County",
    "Vermilion County",
    "Wabash County",
    "Warren County",
    "Washington County",
    "Wayne County",
    "White County",
    "Whiteside County",
    "Will County",
    "Williamson County",
    "Winnebago County",
    "Woodford County"
]

# Filter the DataFrame to include only rows from the specified counties
illinois_counties = df[df['county'].isin(counties_in_illinois)]


In [18]:
illinois_counties

tile_count              county     lat      lon
2646          1.0         Cass County  46.971  -96.959
2647         11.0         Cass County  46.797  -96.914
2648          0.0         Cass County  46.717  -97.043
2649          6.0         Cass County  46.883  -96.861
2650          2.0         Cass County  46.919  -96.792
2651          0.0         Cass County     NaN      NaN
2652          1.0         Cass County  46.855  -96.873
2653          1.0         Cass County  46.869  -96.872
2654          3.0         Cass County  46.868  -96.931
2655          2.0         Cass County  46.934  -96.825
2656          0.0         Cass County  46.898  -96.791
2657          4.0         Cass County  46.879  -96.816
2658          2.0         Cass County  46.877  -96.785
2659          0.0         Cass County  46.868  -96.787
2660          0.0         Cass County  46.868  -96.809
2661          0.0         Cass County  46.856  -96.828
2662          0.0         Cass County  46.913  -96.768
2663          0.0         Cass County  46.857  -96.852
2664          1.0         Cass County  46.874  -96.893
2665          1.0         Cass County  46.858  -96.895
2666          1.0         Cass County  46.818  -96.829
2667          2.0         Cass County  46.840  -96.841
2668          3.0         Cass County  46.827  -96.800
2669          1.0         Cass County  46.814  -96.808
2670          0.0         Cass County  46.884  -96.781
2671          0.0         Cass County  46.886  -96.804
2672          1.0         Cass County  46.855  -96.791
2673          0.0         Cass County     NaN      NaN
2674          0.0         Cass County  46.841  -96.790
2675          1.0         Cass County     NaN      NaN
2676          1.0         Cass County  46.935  -97.505
2677          0.0         Cass County     NaN      NaN
2678          2.0         Cass County  46.934  -97.240
3192          0.0        Wayne County  43.054  -77.227
3193          0.0        Wayne County  43.250  -77.049
3194          3.0        Wayne County  43.203  -77.050
3195          0.0        Wayne County  43.076  -77.022
3196          9.0        Wayne County  43.065  -76.993
3197          0.0        Wayne County  43.249  -76.895
3198          3.0        Wayne County  43.280  -76.772
3199          0.0        Wayne County  43.172  -76.835
3200          2.0        Wayne County  43.040  -77.111
3201          1.0        Wayne County  43.038  -77.076
3202          1.0        Wayne County  43.078  -76.852
3203          0.0        Wayne County  43.084  -76.871
3204          0.0        Wayne County  43.273  -76.971
3205          0.0        Wayne County  43.162  -77.194
3206          0.0        Wayne County  43.163  -77.288
3207          5.0        Wayne County  43.079  -77.342
3208          0.0        Wayne County  43.253  -77.314
3209          3.0        Wayne County  43.217  -77.314
3210          3.0        Wayne County  43.163  -77.344
3211          3.0        Wayne County  43.079  -77.285
3212          1.0        Wayne County  43.260  -77.192
3213          7.0        Wayne County  43.218  -77.193
3214          1.0        Wayne County  43.084  -77.191
3298          3.0   Washington County     NaN      NaN
3299         13.0   Washington County  41.337  -91.821
3300         40.0   Washington County  41.302  -91.685
3301         20.0   Washington County  41.281  -91.688
3302          4.0   Washington County     NaN      NaN
3303          3.0      Calhoun County  42.348  -85.195
3304          0.0      Calhoun County  42.344  -85.226
3305          0.0      Calhoun County  42.356  -85.250
3306          2.0      Calhoun County  42.331  -85.242
3307          3.0      Calhoun County  42.305  -85.242
3308         10.0      Calhoun County  42.272  -85.248
3309          3.0      Calhoun County  42.294  -85.208
3310          3.0      Calhoun County  42.284  -85.189
3311          3.0      Calhoun County  42.265  -85.199
3312          5.0      Calhoun County  42.278  -85.141
3313          3.0      Calhoun County  42.289  

In [ ]:
df123 = df[df['county'].isin(['Cook County'])]

In [14]:
df123 = df[df['county'].isin(['Cook County'])]

In [15]:
filtered_df = df123.query('0<tile_count<100')
filtered_df

tile_count       county     lat     lon
8897          1.0  Cook County  41.770 -87.581
8898         17.0  Cook County  42.146 -87.861
8903          6.0  Cook County  41.935 -87.752
8904          2.0  Cook County  41.876 -87.817
8905          6.0  Cook County  41.978 -87.822
8906          5.0  Cook County  41.900 -87.629
8907         12.0  Cook County  41.983 -87.847
8910          1.0  Cook County  41.761 -87.671
8911         12.0  Cook County  41.663 -87.820
8917          2.0  Cook County  41.777 -87.662
8918          1.0  Cook County  41.790 -87.699
8919          1.0  Cook County  41.710 -87.651
8920          3.0  Cook County  41.949 -87.652
8921          3.0  Cook County  41.921 -87.685
8922          1.0  Cook County  42.073 -87.790
8923          1.0  Cook County  41.714 -87.638
8924          1.0  Cook County  41.790 -87.708
8925          2.0  Cook County  41.715 -87.596
8926          1.0  Cook County  41.622 -87.902
8927          5.0  Cook County  41.700 -87.598
8928          1.0  Cook County  41.761 -87.581
8929          1.0  Cook County  41.689 -87.605
8930          3.0  Cook County  41.990 -87.802
8932          1.0  Cook County  41.640 -87.698
8934          4.0  Cook County  41.912 -87.675
8935          2.0  Cook County  41.912 -87.682
8938          1.0  Cook County  41.735 -87.576
8940          1.0  Cook County  41.905 -87.702
8941          1.0  Cook County  41.628 -87.742
8943          1.0  Cook County  41.987 -87.769
8949          5.0  Cook County  41.970 -87.760
8951          1.0  Cook County  41.622 -87.708
8952          1.0  Cook County  41.761 -87.656
8953          2.0  Cook County  41.903 -87.838
8954          5.0  Cook County  42.099 -87.964
8955          2.0  Cook County  41.900 -87.665
8956          1.0  Cook County  41.900 -87.670
8958          1.0  Cook County  41.900 -87.675
8960         12.0  Cook County  41.899 -87.689
8965          1.0  Cook County  41.892 -87.692
8967          1.0  Cook County  41.892 -87.679
8968          3.0  Cook County  42.099 -87.986
8969          2.0  Cook County  41.892 -87.675
8970          4.0  Cook County  41.936 -87.661
8971          2.0  Cook County  41.892 -87.670
8972          2.0  Cook County  41.892 -87.665
8975          3.0  Cook County  41.893 -87.653
8977          2.0  Cook County  41.953 -87.661
8979          4.0  Cook County  41.879 -87.672
8980          5.0  Cook County  41.936 -87.656
8981          1.0  Cook County  41.817 -87.692
8985          1.0  Cook County  42.075 -87.970
8986          5.0  Cook County  41.714 -87.677
8987          5.0  Cook County  42.075 -87.994
8988         22.0  Cook County  41.740 -87.632
8989          1.0  Cook County  41.566 -87.779
8990          5.0  Cook County  41.998 -88.017
8991          2.0  Cook County  42.025 -88.013
8992          1.0  Cook County  42.026 -87.976
8993          4.0  Cook County  42.081 -87.698
8994          2.0  Cook County  42.009 -87.940
8995          4.0  Cook County  42.030 -87.906
8996         26.0  Cook County  42.011 -87.903
8998         11.0  Cook County  41.986 -87.870
8999          1.0  Cook County  41.971 -87.837
9003          3.0  Cook County  41.781 -87.791
9004          1.0  Cook County  41.798 -87.599
9005          3.0  Cook County  42.082 -88.017
9006          1.0  Cook County  41.713 -87.550
9007          7.0  Cook County  41.815 -87.650
9008          1.0  Cook County  41.716 -87.576
9010          2.0  Cook County  41.626 -87.560
9011          2.0  Cook County  41.912 -87.722
9012          1.0  Cook County  42.075 -88.019
9013          1.0  Cook County  41.952 -87.827
9017          1.0  Cook County  41.820 -87.615
9018          1.0  Cook County  41.798 -87.582
9023          1.0  Cook County  41.842 -87.735
9025          2.0  Cook County  41.809 -87.614
9026          1.0  Cook County  41.972 -87.798
9027          2.0  Cook County  41.856 -87.644
9031          1.0  Cook County  41.806 -87.627
9032          1.0  Cook County  41.906 -87.761
9033          1.0  Cook County  41.804 -87.621
9034        

In [16]:
# df[df['tile_count']<500]
illinois_counties[illinois_counties['tile_count']<500]

tile_count              county     lat      lon
2646          1.0         Cass County  46.971  -96.959
2647         11.0         Cass County  46.797  -96.914
2648          0.0         Cass County  46.717  -97.043
2649          6.0         Cass County  46.883  -96.861
2650          2.0         Cass County  46.919  -96.792
2651          0.0         Cass County     NaN      NaN
2652          1.0         Cass County  46.855  -96.873
2653          1.0         Cass County  46.869  -96.872
2654          3.0         Cass County  46.868  -96.931
2655          2.0         Cass County  46.934  -96.825
2656          0.0         Cass County  46.898  -96.791
2657          4.0         Cass County  46.879  -96.816
2658          2.0         Cass County  46.877  -96.785
2659          0.0         Cass County  46.868  -96.787
2660          0.0         Cass County  46.868  -96.809
2661          0.0         Cass County  46.856  -96.828
2662          0.0         Cass County  46.913  -96.768
2663          0.0         Cass County  46.857  -96.852
2664          1.0         Cass County  46.874  -96.893
2665          1.0         Cass County  46.858  -96.895
2666          1.0         Cass County  46.818  -96.829
2667          2.0         Cass County  46.840  -96.841
2668          3.0         Cass County  46.827  -96.800
2669          1.0         Cass County  46.814  -96.808
2670          0.0         Cass County  46.884  -96.781
2671          0.0         Cass County  46.886  -96.804
2672          1.0         Cass County  46.855  -96.791
2673          0.0         Cass County     NaN      NaN
2674          0.0         Cass County  46.841  -96.790
2675          1.0         Cass County     NaN      NaN
2676          1.0         Cass County  46.935  -97.505
2677          0.0         Cass County     NaN      NaN
2678          2.0         Cass County  46.934  -97.240
3192          0.0        Wayne County  43.054  -77.227
3193          0.0        Wayne County  43.250  -77.049
3194          3.0        Wayne County  43.203  -77.050
3195          0.0        Wayne County  43.076  -77.022
3196          9.0        Wayne County  43.065  -76.993
3197          0.0        Wayne County  43.249  -76.895
3198          3.0        Wayne County  43.280  -76.772
3199          0.0        Wayne County  43.172  -76.835
3200          2.0        Wayne County  43.040  -77.111
3201          1.0        Wayne County  43.038  -77.076
3202          1.0        Wayne County  43.078  -76.852
3203          0.0        Wayne County  43.084  -76.871
3204          0.0        Wayne County  43.273  -76.971
3205          0.0        Wayne County  43.162  -77.194
3206          0.0        Wayne County  43.163  -77.288
3207          5.0        Wayne County  43.079  -77.342
3208          0.0        Wayne County  43.253  -77.314
3209          3.0        Wayne County  43.217  -77.314
3210          3.0        Wayne County  43.163  -77.344
3211          3.0        Wayne County  43.079  -77.285
3212          1.0        Wayne County  43.260  -77.192
3213          7.0        Wayne County  43.218  -77.193
3214          1.0        Wayne County  43.084  -77.191
3298          3.0   Washington County     NaN      NaN
3299         13.0   Washington County  41.337  -91.821
3300         40.0   Washington County  41.302  -91.685
3301         20.0   Washington County  41.281  -91.688
3302          4.0   Washington County     NaN      NaN
3303          3.0      Calhoun County  42.348  -85.195
3304          0.0      Calhoun County  42.344  -85.226
3305          0.0      Calhoun County  42.356  -85.250
3306          2.0      Calhoun County  42.331  -85.242
3307          3.0      Calhoun County  42.305  -85.242
3308         10.0      Calhoun County  42.272  -85.248
3309          3.0      Calhoun County  42.294  -85.208
3310          3.0      Calhoun County  42.284  -85.189
3311          3.0      Calhoun County  42.265  -85.199
3312          5.0      Calhoun County  42.278  -85.141
3313          3.0      Calhoun County  42.289  

In [17]:
from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent="myGeocoder")
location = geolocator.reverse("40.703,-75.151")

GeocoderUnavailable: HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Max retries exceeded with url: /reverse?lat=40.703&lon=-75.151&format=json&addressdetails=1 (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x7acfeccbf2b0>: Failed to establish a new connection: [Errno -3] Temporary failure in name resolution'))

In [ ]:
coordinates = (40.703,-75.151)
reverse_geocode.search(coordinates)

In [ ]:
from geopy.geocoders import Nominatim
locator = Nominatim(user_agent="myGeocoder")

illinois_counties['address'] = illinois_counties.apply(lambda row: locator.reverse((row.lat,row.lon)).address,axis=1)